In [61]:
import pandas as pd
import geopandas as gpd
import numpy as np
from shapely.wkt import loads
from shapely.geometry import Point, Polygon
import seaborn as sns
import geohash_hilbert as ghh

In [12]:
osm_df = pd.read_csv("../data/Stupino_OSM.csv")
osm_df.geometry = osm_df['geometry'].apply(loads)
osm_gdf = gpd.GeoDataFrame(osm_df, geometry='geometry', crs=4326)

In [13]:
osm_gdf.columns

Index(['element_type', 'osmid', 'geometry', 'building', 'nodes',
       'building:levels', 'addr:housenumber', 'addr:street', 'addr:city',
       'name', 'power', 'substation', 'shop', 'ref', 'amenity', 'covered',
       'man_made', 'addr:postcode', 'min_height', 'height', 'opening_hours',
       'type'],
      dtype='object')

In [14]:
osm_gdf.head()

element_type     osmid                                           geometry   
0          way  38149921  POLYGON ((38.08843 54.89178, 38.08841 54.89168...  \
1          way  38150506  POLYGON ((38.08792 54.88927, 38.08812 54.88926...   
2          way  96695125  POLYGON ((38.08118 54.89339, 38.08129 54.89400...   
3          way  96695127  POLYGON ((38.08185 54.89397, 38.08205 54.89396...   
4          way  96695129  POLYGON ((38.08257 54.89392, 38.08277 54.89391...   

     building                                              nodes   
0  apartments  [449063448, 449063449, 449063450, 449063451, 4...  \
1  apartments  [449069926, 449069927, 4294693489, 4294693488,...   
2  apartments  [1119809344, 1119809343, 1119809359, 433084688...   
3  apartments  [1119809355, 1119809351, 4330846905, 433084690...   
4  apartments  [1119809358, 1119809348, 1119809349, 111980935...   

  building:levels addr:housenumber        addr:street addr:city name  ...   
0               5                5   улица Тимирязева   Ступино  NaN  ...  \
1               5            18/19    улица Тургенева   Ступино  NaN  ...   
2               5               43  Октябрьская улица   Ступино  NaN  ...   
3               5               41  Октябрьская улица   Ступино  NaN  ...   
4               5               39  Октябрьская улица   Ступино  NaN  ...   

  shop  ref amenity covered man_made addr:postcode min_height  height   
0  NaN  NaN     NaN     NaN      NaN           NaN        NaN     NaN  \
1  NaN  NaN     NaN     NaN      NaN           NaN        NaN     NaN   
2  NaN  NaN     NaN     NaN      NaN           NaN        NaN     NaN   
3  NaN  NaN     NaN     NaN      NaN           NaN        NaN     NaN   
4  NaN  NaN     NaN     NaN      NaN           NaN        NaN     NaN   

  opening_hours  type  
0           NaN   NaN  
1           NaN   NaN  
2           NaN   NaN  
3           NaN   NaN  
4           NaN   NaN  

[5 rows x 22 columns]

In [15]:
osm_gdf[['building', 'geometry']].explore(categorical=True, column='building')

In [16]:
hw = pd.read_csv("labeled_cluster_data.csv", index_col=0)
hw1 = pd.read_csv("..\\data\\2023-05-13_15-49-08\\labeled_cluster_data_2023-05-13_15-49-08.csv", index_col=0)

In [17]:
hw1.head()

id      lat      lon  cluster  cluster_size           inq  wd_rate   
0   2.0  54.8436  38.1929      0.0        5056.0  46681.775000     1.00  \
1   6.0  54.9034  38.0696      0.0         989.0  15146.533333     0.75   
2   6.0  54.8933  38.0780      1.0         830.0  39723.665414     1.00   
5  13.0  54.8428  38.1908      0.0        2908.0  38369.617647     1.00   
6  14.0  54.8419  38.1885      0.0        2213.0  35349.094340     1.00   

     wd_all  work_place  
0  1.000000       False  
1  0.428571        True  
2  0.571429        True  
5  1.000000       False  
6  1.000000       False

In [18]:
hw.shape

(2624, 10)

In [19]:
geometry = [Point(xy) for xy in zip(hw['lon'], hw['lat'])]
hw_gdf = gpd.GeoDataFrame(hw, geometry=geometry, crs=4326)
hw_gdf.explore(categorical=True, column='work_place', cmap=['blue', 'green'])

In [20]:
hw_osm = hw_gdf.sjoin_nearest(osm_gdf, how="left", rsuffix='2')
living = hw_osm[hw_osm['building'].isin(['apartments', 'house', 'residential'])]
working = hw_osm[~hw_osm['building'].isin(['apartments', 'house', 'residential'])]

c:\anaconda3\lib\site-packages\geopandas\array.py:344: UserWarning: Geometry is in a geographic CRS. Results from 'sjoin_nearest' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  warnings.warn(


In [21]:
hw_osm.columns

Index(['id', 'lat', 'lon', 'cluster', 'cluster_size', 'inq', 'wd_rate',
       'wd_all', 'work_place', 'geometry', 'index_2', 'element_type', 'osmid',
       'building', 'nodes', 'building:levels', 'addr:housenumber',
       'addr:street', 'addr:city', 'name', 'power', 'substation', 'shop',
       'ref', 'amenity', 'covered', 'man_made', 'addr:postcode', 'min_height',
       'height', 'opening_hours', 'type'],
      dtype='object')

In [22]:
living.head()

id      lat      lon  cluster  cluster_size           inq  wd_rate   
0   2.0  54.8436  38.1929      0.0        5056.0  46681.775000      1.0  \
2   6.0  54.8933  38.0780      1.0         830.0  39723.665414      1.0   
5  13.0  54.8428  38.1908      0.0        2908.0  38369.617647      1.0   
6  14.0  54.8419  38.1885      0.0        2213.0  35349.094340      1.0   
8  27.0  54.8848  38.0623      0.0       16631.0  38301.278897      1.0   

     wd_all  work_place                   geometry  ...  shop  ref  amenity   
0  1.000000       False  POINT (38.19290 54.84360)  ...   NaN  NaN      NaN  \
2  0.571429        True  POINT (38.07800 54.89330)  ...   NaN  NaN      NaN   
5  1.000000       False  POINT (38.19080 54.84280)  ...   NaN  NaN      NaN   
6  1.000000       False  POINT (38.18850 54.84190)  ...   NaN  NaN      NaN   
8  1.000000       False  POINT (38.06230 54.88480)  ...   NaN  NaN      NaN   

  covered man_made addr:postcode min_height height opening_hours type  
0     NaN      NaN           NaN        NaN    NaN           NaN  NaN  
2     NaN      NaN           NaN        NaN    NaN           NaN  NaN  
5     NaN      NaN           NaN        NaN    NaN           NaN  NaN  
6     NaN      NaN           NaN        NaN    NaN           NaN  NaN  
8     NaN      NaN           NaN        NaN    NaN           NaN  NaN  

[5 rows x 32 columns]

In [57]:
hw_osm['hash'] = hw_osm[['lat', 'lon']].apply(lambda x: ghh.encode(x['lon'], x['lat'], precision=18, bits_per_char=2, ), axis=1)

In [62]:
geometry = [Polygon(
                ghh.rectangle(hash, bits_per_char=18)['geometry']['coordinates']
                ) 
                for hash in zip(hw_osm['hash'])
            ]
geohashes = gpd.GeoDataFrame(hw_osm['hash'])

AssertionError: 

{'type': 'Feature',
 'properties': {'code': '210123101103233300',
  'lng': 38.19328308105469,
  'lat': 54.843406677246094,
  'lng_err': 0.0006866455078125,
  'lat_err': 0.00034332275390625,
  'bits_per_char': 2},
 'bbox': (38.192596435546875, 54.84306335449219, 38.1939697265625, 54.84375),
 'geometry': {'type': 'Polygon',
  'coordinates': [[(38.192596435546875, 54.84306335449219),
    (38.1939697265625, 54.84306335449219),
    (38.1939697265625, 54.84375),
    (38.192596435546875, 54.84375),
    (38.192596435546875, 54.84306335449219)]]}}